# CMIP6 storage
with `panel`, `pandas` and `hvplot`

The primary publication of national Earth System Model data at DKRZ takes the largest part of the CMIP Data Pool (CDP). Most of the data have been produced within the national CMIP Project [DICAD](https://www.dkrz.de/c6de) and in the compute project RZ988. 

DKRZ supports modeling groups in all steps of the data wokflow from **preparation** to **publication**. In order to track and display the effort for this data workflow, we run automated scripts (*cronjobs*) which capture the extent of the final product: the disk space usage of these groups in the data pool and update it daily. The resulting statistics are uploaded into a public and freely available [swift storage](https://swiftbrowser.dkrz.de/public/dkrz_a44962e3ba914c309a7421573a6949a6/Pool-Statistics/). 

In the following, we create *responsive* bar plots with `pandas`, `pandas` and `hvplot` for statistical Key Performance Indicators of the CDP.

## German contribution and publication

Here we present you statistics of DICAD contributions to the CDP. Datasets which were

- created as part of DICAD and
- have been primarily published at the DKRZ ESGF Node 

are considered.

The statisctis are computed by grouping the measures by:

- **source_id**: Earth System Models (ESM)s which have contributed to the CDP.
- **institution_id**: Institutions which have conducted and submitted model simulations to the CDP.
- **publication type**: How much data has been published and replicated at DKRZ ESGF node.

In [ ]:
import warnings
warnings.filterwarnings('ignore')
kpis=["size [TB]", "filenumber","datasets"]

In [ ]:
import panel as pn
pn.extension("tabulator")
import pandas as pd
sourcesumdf = pd.read_csv("https://swift.dkrz.de/v1/dkrz_a44962e3ba914c309a7421573a6949a6/Pool-Statistics/mistral-cmip6-allocation-by-source.csv.gz").sort_values("size", ascending=False)
allinstdf = pd.read_csv("https://swift.dkrz.de/v1/dkrz_a44962e3ba914c309a7421573a6949a6/Pool-Statistics/mistral-cmip6-allocation-by-dicad-institutes.csv.gz").sort_values("size", ascending=False)
allreplicadf = pd.read_csv("https://swift.dkrz.de/v1/dkrz_a44962e3ba914c309a7421573a6949a6/Pool-Statistics/mistral-cmip6-allocation-by-publicationType.csv.gz").sort_values("size", ascending=False)

In [ ]:
import intake
from pathlib import Path
import hvplot.pandas
from bokeh.models import NumeralTickFormatter
import pandas as pd
sourcesumdf["Group"]="By source_id"
sourcesumdf["Key"]="source_id"
sourcesumdf["Legend"]=sourcesumdf["source_id"]
allinstdf["Group"]="By institution_id"
allinstdf["Key"]="institution_id"
allinstdf["Legend"]=allinstdf["institution_id"]
allreplicadf["Group"]="By Publication Status"
allreplicadf["Key"]="publicationType"
allreplicadf["Legend"]=allreplicadf["publicationType"]

sourcesumdf=sourcesumdf.set_index("Group")
allinstdf=allinstdf.set_index("Group")
allreplicadf=allreplicadf.set_index("Group")
#
#plotdf=sourcesumrz.append(allinstdf).append(sourcesum).append(allreplica) #.append(expdf)
plotdf=pd.concat([sourcesumdf,allinstdf,allreplicadf])

In [ ]:
plotdf=plotdf.rename(columns={"size":"size [TB]"})
grouped_df=plotdf.groupby(["Key"])

In [ ]:
plot_group=grouped_df.get_group("institution_id").sort_values("filenumber", ascending=False)

In [ ]:
plot_group

In [ ]:
def create_plot(group, kpi):
    global grouped_df
    plot_group=grouped_df.get_group(group).sort_values(kpi, ascending=False)
    a=plot_group.hvplot.bar(y=kpi,
                         ylabel=f"Sum of {kpi} in the CMIP6 Data Pool",
                         xlabel="Group",
                         by="Legend",
                         stacked=False,
                         #grid=True,
                         yformatter=NumeralTickFormatter(format='0,0'),
                         title="",
                         #  legend="top_left",
                           fontsize={'legend': "10%"},
                          width=650,
                          height=500,
                          muted_alpha=0,
                           fontscale=1.2
                          )
    b=plot_group.hvplot.bar(y=kpi,
                         ylabel="",
                         xlabel="Group",
                         by="Legend",
                         stacked=True,
                         #grid=True,
                         yformatter=NumeralTickFormatter(format='0,0'),
                         title="",
                         legend=False,
                           fontsize={'legend': "10%"},
                          width=150,
                          height=500,
                          muted_alpha=0,
                           fontscale=1.2
                          )
    return a+b

In [ ]:
interact = pn.interact(create_plot, group=list(grouped_df.groups.keys()), kpi=kpis)
pn.Column(pn.Card(interact[0], title="Plots for different <i>groups and kpis</i>", styles=dict(background='WhiteSmoke')),
          interact[1]
         ).embed()

The German contribution to CMIP6 by the five sources of **MPI-M** and **AWI** comprises

- 1.6PB of data primary published at dkrz
- more than 33% of the CMIP6 data pool
- 2Mio files or 250 000 datasets

### Statistics for different *source_id*

The file `mistral-cmip6-allocation-by-source.csv.gz` contains the results per source with an additional classification by experiment.

- **MPI-ESM1-2-HR**: The high resolution version of the MPI-ESM1-2. [CV-entry](https://github.com/WCRP-CMIP/CMIP6_CVs/blob/20ef5bb121bdf50fc00ba5b2520298fd4766ffa9/CMIP6_source_id.json#L5621)\*, [Citation example](https://doi.org/10.22033/ESGF/CMIP6.4403)
- **MPI-ESM1-2-LR**: The lower resolution version of the MPI-ESM1-2. [CV-entry](https://github.com/WCRP-CMIP/CMIP6_CVs/blob/20ef5bb121bdf50fc00ba5b2520298fd4766ffa9/CMIP6_source_id.json#L5682)\*, [Citation example](https://doi.org/10.22033/ESGF/CMIP6.6693)
- **AWI-CM-1-1-MR**: [CV-entry](https://github.com/WCRP-CMIP/CMIP6_CVs/blob/20ef5bb121bdf50fc00ba5b2520298fd4766ffa9/CMIP6_source_id.json#L311)\*, [Citation example](https://doi.org/10.22033/ESGF/CMIP6.376)
- **AWI-ESM-1-1-LR**: [CV-entry](https://github.com/WCRP-CMIP/CMIP6_CVs/blob/20ef5bb121bdf50fc00ba5b2520298fd4766ffa9/CMIP6_source_id.json#L475)\*, [Citation example](https://doi.org/10.22033/ESGF/CMIP6.9328)
- **ICON-ESM-LR**: [CV-entry](https://github.com/WCRP-CMIP/CMIP6_CVs/blob/20ef5bb121bdf50fc00ba5b2520298fd4766ffa9/CMIP6_source_id.json#L4569)\*, [Citation example](https://doi.org/10.22033/ESGF/CMIP6.743)

\* *CV* link to the registration in the official [CMIP6 Controlled Vocabulay](https://github.com/WCRP-CMIP/CMIP6_CVs/) where all CMIP6 models had to register.
    
As soon as CMIP6 data from other ESMs like *EMAC-2-53* is available, the lists will be expanded correspondingly.

In [ ]:
tabsource=pn.widgets.Tabulator(sourcesumdf, height=200)
filenamesource, buttonsource = tabsource.download_menu(
    text_kwargs={'name': 'Enter filename', 'value': 'mistral-cmip6-dicad-sources.csv.csv', 'width':100, 'height':60},
    button_kwargs={'name': 'Download table','width':100, 'height':60}
)
pn.Row(pn.Column(filenamesource,buttonsource),tabsource).embed()

### Statistics for different *institution_id*s

The file `mistral-cmip6-allocation-by-dicad-institutes.csv.gz` contains statistics grouped by **institutes** that have contributed to DICAD.

In [ ]:
tabinst=pn.widgets.Tabulator(allinstdf, height=200)
filenameinst, buttoninst = tabinst.download_menu(
    text_kwargs={'name': 'Enter filename', 'value': 'mistral-cmip6-dicad-institutes.csv', 'width':100, 'height':60},
    button_kwargs={'name': 'Download table','width':100, 'height':60}
)
pn.Row(pn.Column(filenameinst, buttoninst),tabinst).embed()

### Statistics for different *publication type*s

The file `mistral-cmip6-allocation-by-publicationType.csv.gz` contains statistics grouped by **institutes** that have contributed to DICAD

- *published originals*:    Data which has been published first at the esgf-node at dkrz and is still valid and available.
- *retracted originals*:    Data which has been published first at the esgf-node at dkrz but has also been retracted afterwards.
- *published replicas*:     Data which has been copied to and published at dkrz and is still valid and available.
- *retracted replicas*:     Data which has been copied to and published at dkrz but has also been retracted afterwards.

In [ ]:
tabrepl=pn.widgets.Tabulator(allreplicadf, height=200)
filenamerepl, buttonrepl = tabrepl.download_menu(
    text_kwargs={'name': 'Enter filename', 'value': 'mistral-cmip6-replica.csv.csv', 'width':100, 'height':60},
    button_kwargs={'name': 'Download table','width':100, 'height':60}
)
pn.Row(pn.Column(filenamerepl, buttonrepl),tabrepl).embed()

In [ ]:
timeseries=pd.read_csv("https://swift.dkrz.de/v1/dkrz_a44962e3ba914c309a7421573a6949a6/Pool-Statistics/mistral-cmip6-allocation-timeseries.csv.gz",
                       parse_dates=True,
                       index_col=0
                        )
tmplot= timeseries.hvplot.line(y=["Disk Allocation [GB]", "Number of Datasets", "Number of Files"],
                               shared_axes=False,
                               yformatter=NumeralTickFormatter(format='0,0'),
                               grid=True,
                               width=600,
                               height=500,
                               legend="top_left",
                              ).opts(axiswise=True)
hvplot.save(tmplot,"pool-timeseries-hvplot.html")

In [ ]:
tmplot

### Cloud upload

We use the `swiftclient` for the upload.

In [ ]:
#from swiftclient import client
#from swiftenvbk0988 import *
#
#with open("pool-statistics-hvplot.html", 'rb') as f:
#    client.put_object(OS_STORAGE_URL, OS_AUTH_TOKEN, "Pool-Statistics", "pool-statistics-hvplot.html", f)
#with open("pool-timeseries-hvplot.html", 'rb') as f:
#    client.put_object(OS_STORAGE_URL, OS_AUTH_TOKEN, "Pool-Statistics", "pool-timeseries-hvplot.html", f)